In [ ]:
import pandas as pd
from sklearn.utils.class_weight import compute_class_weight
import numpy as np
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras import models
from tensorflow.keras import layers
from matplotlib import pyplot as plt
from keras.models import load_model
from mlxtend.plotting import plot_confusion_matrix
from sklearn.metrics import confusion_matrix
from sklearn.metrics import roc_curve
from sklearn.metrics import roc_auc_score
import plotly.graph_objects as go
from math import sqrt
import warnings
from scipy import stats
warnings.filterwarnings('ignore')

In [ ]:
df=pd.read_stata('NSDUH_2020.dta')
df['BMI2']=pd.to_numeric(df['BMI2'], errors='coerce')

df['NEWRACE2'] = df['NEWRACE2'].replace('1 - NonHisp White','White')
df['NEWRACE2'] = df['NEWRACE2'].replace('2 - NonHisp Black/Afr Am','Black')
df['NEWRACE2'] = df['NEWRACE2'].replace('3 - NonHisp Native Am/AK Native','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('4 - NonHisp Native HI/Other Pac Isl','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('5 - NonHisp Asian','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('6 - NonHisp more than one race','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('7 - Hispanic','Others')

data=df[['NEWRACE2', 'INCOME' ,'ADDPREV','OXCOPDAPYU', 'OXYMPDAPYU', 'HYDCPDAPYU', 'HYDMPDAPYU', 'FENTPDAPYU',
         'MORPPDAPYU', 'CODEPDAPYU', 'MTDNPDAPYU', 'TRAMPDAPYU', 'BUPRPDAPYU',
         'HEREVER','TXEVRRCVD','DIABETEVR', 'COPDEVER', 'CIRROSEVR', 'HEPBCEVER',
         'KIDNYDSEV', 'ASTHMAEVR', 'HIVAIDSEV', 'CANCEREVR','IRSEX', 'IRMARIT', 'WRK35WKUS', 'UDPYOPI']]

data=pd.get_dummies(data)

data=data.drop(['INCOME_2 - $20,000 - $49,999', 'INCOME_3 - $50,000 - $74,999',  'INCOME_4 - $75,000 or More', 'ADDPREV_85 - BAD DATA Logically assigned', 'ADDPREV_94 - DON T KNOW', 'ADDPREV_97 - REFUSED', 'ADDPREV_98 - BLANK',
                'ADDPREV_99 - LEGITIMATE SKIP', 'IRSEX_2 - Female',
                'OXCOPDAPYU_0 - No/Unknown', 'OXYMPDAPYU_0 - No/Unknown', 'HYDCPDAPYU_0 - No/Unknown', 'HYDMPDAPYU_0 - No/Unknown',
               'FENTPDAPYU_0 - No/Unknown', 'MORPPDAPYU_0 - No/Unknown', 'CODEPDAPYU_0 - No/Unknown', 'MTDNPDAPYU_0 - No/Unknown',
               'TRAMPDAPYU_0 - No/Unknown', 'BUPRPDAPYU_0 - No/Unknown', 'HEREVER_94 - DON T KNOW',
'HEREVER_97 - REFUSED', 'TXEVRRCVD_85 - BAD DATA Logically assigned',
'TXEVRRCVD_91 - NEVER USED ALCOHOL OR DRUGS','TXEVRRCVD_94 - DON T KNOW','TXEVRRCVD_97 - REFUSED','TXEVRRCVD_98 - BLANK',
                'DIABETEVR_85 - BAD DATA Logically assigned'
,'DIABETEVR_94 - DON T KNOW','DIABETEVR_97 - REFUSED','DIABETEVR_98 - BLANK','DIABETEVR_99 - LEGITIMATE SKIP',
                'COPDEVER_85 - BAD DATA Logically assigned','COPDEVER_94 - DON T KNOW','COPDEVER_97 - REFUSED'
,'COPDEVER_98 - BLANK','COPDEVER_99 - LEGITIMATE SKIP', 'CIRROSEVR_85 - BAD DATA Logically assigned'
,'CIRROSEVR_94 - DON T KNOW','CIRROSEVR_97 - REFUSED','CIRROSEVR_98 - BLANK','CIRROSEVR_99 - LEGITIMATE SKIP',
                'HEPBCEVER_85 - BAD DATA Logically assigned','HEPBCEVER_94 - DON T KNOW','HEPBCEVER_97 - REFUSED'
,'HEPBCEVER_98 - BLANK','HEPBCEVER_99 - LEGITIMATE SKIP'
,'KIDNYDSEV_85 - BAD DATA Logically assigned','KIDNYDSEV_94 - DON T KNOW','KIDNYDSEV_97 - REFUSED','KIDNYDSEV_98 - BLANK'
,'KIDNYDSEV_99 - LEGITIMATE SKIP','ASTHMAEVR_85 - BAD DATA Logically assigned','ASTHMAEVR_94 - DON T KNOW','ASTHMAEVR_97 - REFUSED',
'ASTHMAEVR_98 - BLANK','ASTHMAEVR_99 - LEGITIMATE SKIP', 'HIVAIDSEV_85 - BAD DATA Logically assigned'
,'HIVAIDSEV_94 - DON T KNOW','HIVAIDSEV_97 - REFUSED','HIVAIDSEV_98 - BLANK','HIVAIDSEV_99 - LEGITIMATE SKIP',
              'CANCEREVR_85 - BAD DATA Logically assigned','CANCEREVR_94 - DON T KNOW','CANCEREVR_97 - REFUSED'
,'CANCEREVR_98 - BLANK','CANCEREVR_99 - LEGITIMATE SKIP'
,'WRK35WKUS_85 - BAD DATA Logically assigned','WRK35WKUS_94 - DON T KNOW','WRK35WKUS_97 - REFUSED','WRK35WKUS_98 - BLANK'
,'WRK35WKUS_99 - LEGITIMATE SKIP', 'UDPYOPI_0 - No', 'IRMARIT_99 - LEGITIMATE SKIP Respondent is <= 14 years old'
               ], axis=1)

data

NEWRACE2_White  NEWRACE2_Black  NEWRACE2_Others  \
0                True           False            False   
1                True           False            False   
2               False           False             True   
3                True           False            False   
4                True           False            False   
...               ...             ...              ...   
32888            True           False            False   
32889            True           False            False   
32890           False           False             True   
32891            True           False            False   
32892            True           False            False   

       INCOME_1 - Less than $20,000  ADDPREV_1 - Yes  ADDPREV_2 - No  \
0                             False            False            True   
1                             False            False            True   
2                             False             True           False   
3                             False            False            True   
4                             False            False           False   
...                             ...              ...             ...   
32888                         False             True           False   
32889                         False             True           False   
32890                         False            False           False   
32891                         False             True           False   
32892                         False             True           False   

       OXCOPDAPYU_1 - Yes  OXYMPDAPYU_1 - Yes  HYDCPDAPYU_1 - Yes  \
0                   False               False               False   
1                   False               False                True   
2                   False               False                True   
3                   False               False               False   
4                   False               False               False   
...                   ...                 ...                 ...   
32888               False               False               False   
32889               False               False               False   
32890               False               False               False   
32891               False               False               False   
32892               False               False                True   

       HYDMPDAPYU_1 - Yes  ...  CANCEREVR_1 - Yes  CANCEREVR_2 - No  \
0                   False  ...              False              True   
1                   False  ...              False             False   
2                   False  ...              False             False   
3                   False  ...              False              True   
4                   False  ...              False              True   
...                   ...  ...                ...               ...   
32888               False  ...              False              True   
32889               False  ...              False              True   
32890               False  ...              False             False   
32891               False  ...              False             False   
32892               False  ...              False              True   

       IRSEX_1 - Male  IRMARIT_1 - Married  IRMARIT_2 - Widowed  \
0                True                False                False   
1                True                False                False   
2               False                False                False   
3                True                 True                False   
4                True                False                False   
...               ...                  ...                  ...   
32888            True                False                False   
32889            True                 True                False   
32890           False                False                False   
32891           False                False                False   
32892           False     

In [ ]:
d_pos=data[data['UDPYOPI_1 - Yes'].isin([1])]
d_neg=data[data['UDPYOPI_1 - Yes'].isin([0])]
data=pd.concat([d_pos, d_neg])

X=data.drop(['UDPYOPI_1 - Yes'], axis=1)
y=data['UDPYOPI_1 - Yes']
X=X.astype(float)
y=y.astype(float)
df1=df[['BMI2']]
df1=df1.astype(float)
X=pd.concat([X, df1], axis=1)

X=X.fillna(0)

In [ ]:
data=pd.concat([X, y], axis=1)
data=data.dropna()

In [ ]:
data

NEWRACE2_White  NEWRACE2_Black  NEWRACE2_Others  \
193               1.0             0.0              0.0   
258               1.0             0.0              0.0   
430               0.0             0.0              1.0   
776               1.0             0.0              0.0   
887               1.0             0.0              0.0   
...               ...             ...              ...   
32888             1.0             0.0              0.0   
32889             1.0             0.0              0.0   
32890             0.0             0.0              1.0   
32891             1.0             0.0              0.0   
32892             1.0             0.0              0.0   

       INCOME_1 - Less than $20,000  ADDPREV_1 - Yes  ADDPREV_2 - No  \
193                             0.0              0.0             0.0   
258                             0.0              1.0             0.0   
430                             0.0              0.0             0.0   
776                             0.0              1.0             0.0   
887                             0.0              1.0             0.0   
...                             ...              ...             ...   
32888                           0.0              1.0             0.0   
32889                           0.0              1.0             0.0   
32890                           0.0              0.0             0.0   
32891                           0.0              1.0             0.0   
32892                           0.0              1.0             0.0   

       OXCOPDAPYU_1 - Yes  OXYMPDAPYU_1 - Yes  HYDCPDAPYU_1 - Yes  \
193                   1.0                 0.0                 1.0   
258                   1.0                 0.0                 1.0   
430                   1.0                 0.0                 1.0   
776                   0.0                 0.0                 0.0   
887                   0.0                 0.0                 0.0   
...                   ...                 ...                 ...   
32888                 0.0                 0.0                 0.0   
32889                 0.0                 0.0                 0.0   
32890                 0.0                 0.0                 0.0   
32891                 0.0                 0.0                 0.0   
32892                 0.0                 0.0                 1.0   

       HYDMPDAPYU_1 - Yes  ...  CANCEREVR_2 - No  IRSEX_1 - Male  \
193                   0.0  ...               0.0             0.0   
258                   0.0  ...               1.0             1.0   
430                   0.0  ...               0.0             1.0   
776                   0.0  ...               1.0             0.0   
887                   0.0  ...               0.0             1.0   
...                   ...  ...               ...             ...   
32888                 0.0  ...               1.0             1.0   
32889                 0.0  ...               1.0             1.0   
32890                 0.0  ...               0.0             0.0   
32891                 0.0  ...               0.0             0.0   
32892                 0.0  ...               1.0             0.0   

       IRMARIT_1 - Married  IRMARIT_2 - Widowed  \
193                    0.0                  0.0   
258                    1.0                  0.0   
430                    0.0                  0.0   
776                    0.0                  0.0   
887                    0.0                  0.0   
...                    ...                  ...   
32888                  0.0                  0.0   
32889                  1.0                  0.0   
32890                  0.0                  0.0   
32891                  0.0                  0.0   
32892                  0.0                  0.0   

       IRMARIT_3 - Divorced or Separated  IRMARIT_4 - Never Been Married  \
193                                  0.0                             1.0   
258                               

In [ ]:
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import NearestNeighbors

features = ['NEWRACE2_White', 'NEWRACE2_Black', 'NEWRACE2_Others',
            'INCOME_1 - Less than $20,000', 'IRSEX_1 - Male', 'IRMARIT_1 - Married',
            'IRMARIT_2 - Widowed', 'IRMARIT_3 - Divorced or Separated',
            'IRMARIT_4 - Never Been Married', 'WRK35WKUS_1 - Yes',
            'WRK35WKUS_2 - No', 'BMI2']

X_control = data[features]
model = LogisticRegression()
model.fit(X_control, y)
data['propensity_score'] = model.predict_proba(X_control)[:, 1]

treated = data[data['UDPYOPI_1 - Yes'] == 1]
control = data[data['UDPYOPI_1 - Yes'] == 0]

nn = NearestNeighbors(n_neighbors=158)
nn.fit(control[['propensity_score']])
distances, indices = nn.kneighbors(treated[['propensity_score']])

matched_indices = indices.flatten()
matched_control = control.iloc[matched_indices]
matched_data = pd.concat([treated, matched_control])

counts = matched_data['UDPYOPI_1 - Yes'].value_counts()
number_of_OUD_cases = counts.get(1, 0)
number_of_non_OUD_cases = counts.get(0, 0)

print(f"Number of OUD (treatment) cases after matching: {number_of_OUD_cases}")
print(f"Number of non-OUD (control) cases after matching: {number_of_non_OUD_cases}")

if number_of_non_OUD_cases > number_of_OUD_cases:
    print("Class 0 (non-OUD) is the control group, and there are more control cases than treatment cases after matching.")
else:
    print("Class 1 (OUD) is the treatment group, and the matching has resulted in more treatment cases.")


Number of OUD (treatment) cases after matching: 207
Number of non-OUD (control) cases after matching: 32706
Class 0 (non-OUD) is the control group, and there are more control cases than treatment cases after matching.


In [ ]:
matched_data_full = data.loc[matched_data.index]

matched_data_full

NEWRACE2_White  NEWRACE2_Black  NEWRACE2_Others  \
193               1.0             0.0              0.0   
258               1.0             0.0              0.0   
430               0.0             0.0              1.0   
776               1.0             0.0              0.0   
887               1.0             0.0              0.0   
...               ...             ...              ...   
17296             1.0             0.0              0.0   
23435             1.0             0.0              0.0   
21424             1.0             0.0              0.0   
18179             1.0             0.0              0.0   
31203             1.0             0.0              0.0   

       INCOME_1 - Less than $20,000  ADDPREV_1 - Yes  ADDPREV_2 - No  \
193                             0.0              0.0             0.0   
258                             0.0              1.0             0.0   
430                             0.0              0.0             0.0   
776                             0.0              1.0             0.0   
887                             0.0              1.0             0.0   
...                             ...              ...             ...   
17296                           0.0              0.0             0.0   
23435                           1.0              1.0             0.0   
21424                           1.0              0.0             1.0   
18179                           1.0              0.0             1.0   
31203                           0.0              0.0             0.0   

       OXCOPDAPYU_1 - Yes  OXYMPDAPYU_1 - Yes  HYDCPDAPYU_1 - Yes  \
193                   1.0                 0.0                 1.0   
258                   1.0                 0.0                 1.0   
430                   1.0                 0.0                 1.0   
776                   0.0                 0.0                 0.0   
887                   0.0                 0.0                 0.0   
...                   ...                 ...                 ...   
17296                 0.0                 0.0                 0.0   
23435                 0.0                 0.0                 0.0   
21424                 0.0                 0.0                 0.0   
18179                 0.0                 0.0                 0.0   
31203                 0.0                 0.0                 0.0   

       HYDMPDAPYU_1 - Yes  ...  IRSEX_1 - Male  IRMARIT_1 - Married  \
193                   0.0  ...             0.0                  0.0   
258                   0.0  ...             1.0                  1.0   
430                   0.0  ...             1.0                  0.0   
776                   0.0  ...             0.0                  0.0   
887                   0.0  ...             1.0                  0.0   
...                   ...  ...             ...                  ...   
17296                 0.0  ...             0.0                  0.0   
23435                 0.0  ...             0.0                  0.0   
21424                 0.0  ...             0.0                  0.0   
18179                 0.0  ...             0.0                  0.0   
31203                 0.0  ...             0.0                  0.0   

       IRMARIT_2 - Widowed  IRMARIT_3 - Divorced or Separated  \
193                    0.0                                0.0   
258                    0.0                                0.0   
430                    0.0                                0.0   
776                    0.0                                1.0   
887                    0.0                                0.0   
...                    ...                                ...   
17296                  0.0                                0.0   
23435                  0.0                                0.0   
21424                  0.0                                0.0   
18179                  0.0                                0.0   
31203                  0.0                      

In [ ]:
d_pos=matched_data_full[matched_data_full['UDPYOPI_1 - Yes'].isin([1])]
d_neg=matched_data_full[matched_data_full['UDPYOPI_1 - Yes'].isin([0])]
matched_data_full=pd.concat([d_pos, d_neg])

X=matched_data_full.drop(['UDPYOPI_1 - Yes', 'propensity_score'], axis=1)
y=matched_data_full['UDPYOPI_1 - Yes']

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=43, stratify=y) # Use stratify to have the same proportion of each class

class_weights = compute_class_weight(
                                        class_weight = "balanced",
                                        classes = np.unique(y_train),
                                        y = y_train
                                    )
sklearn_weights = dict(enumerate(class_weights))
sklearn_weights

{0: 0.5031722978137899, 1: 79.30722891566265}

In [ ]:
network_sgd = load_model('best_model_sgd.h5')
network_adam = load_model('best_model_adam.h5')

In [ ]:
from sklearn.linear_model import LogisticRegression
logit = LogisticRegression(max_iter=1000000, class_weight=sklearn_weights)
logit_model=logit.fit(X_train, y_train)

In [ ]:
import pickle
filename = 'LR.sav'

with open(filename, 'wb') as file:
    pickle.dump(logit_model, file)

In [ ]:
from sklearn.svm import LinearSVC
svc_linear=LinearSVC(C=1, class_weight=sklearn_weights, dual=False, max_iter=1000000)
svc_linear=svc_linear.fit(X_train, y_train)

In [ ]:
filename = 'SVC_Linear.sav'

with open(filename, 'wb') as file:
    pickle.dump(svc_linear, file)

In [ ]:
from sklearnex import patch_sklearn
patch_sklearn()

Intel(R) Extension for Scikit-learn* enabled (https://github.com/intel/scikit-learn-intelex)


In [ ]:
from sklearn.svm import SVC
svc_rbf = SVC(C=1, kernel='rbf', class_weight=sklearn_weights, probability=True, max_iter=1000000)
svc_rbf = svc_rbf.fit(X_train, y_train)

In [ ]:
filename = 'SVC_RBF.sav'

with open(filename, 'wb') as file:
    pickle.dump(svc_rbf, file)

In [ ]:
preds_sgd=network_sgd.predict(X_test)
preds_adam=network_adam.predict(X_test)
preds_lr=logit_model.predict_proba(X_test)
preds_svc_linear=svc_linear._predict_proba_lr(X_test)
preds_svc_rbf=svc_rbf.predict_proba(X_test)

206/206 [==============================] - 2s 8ms/step


In [ ]:
def plot_roc_curve(true_y1, y_prob1, true_y2, y_prob2, true_y3, y_prob3,true_y4, y_prob4,true_y5, y_prob5,name1, name2, name3, name4, name5, positive=1):
    c_fill      = 'rgba(52, 152, 219, 0.2)'
    c_line      = 'rgba(52, 152, 219, 0.5)'
    c_line_main1 = 'rgba(250, 50, 50, 1.0)'
    c_line_main2 = 'rgba(50, 50, 250, 1.0)'
    c_line_main3 = 'rgba(20, 250, 50, 1.0)'
    c_line_main4 = 'rgba(255, 165, 0, 1.0)'
    c_line_main5 = 'rgba(0, 0, 0, 1.0)'
    c_grid      = 'rgba(5, 5, 5, 0.5)'
    c_annot     = 'rgba(149, 165, 166, 0.5)'
    c_i = 'rgba(255, 255, 255, 0)'
    c_highlight = 'rgba(192, 57, 43, 1.0)'
    AUC1 = roc_auc_score(true_y1, y_prob1)
    N1 = sum(true_y1 == positive)
    N2 = sum(true_y1 != positive)
    Q1 = AUC1 / (2 - AUC1)
    Q2 = 2*AUC1**2 / (1 + AUC1)
    SE_AUC1 = sqrt((AUC1*(1 - AUC1) + (N1 - 1)*(Q1 - AUC1**2) + (N2 - 1)*(Q2 - AUC1**2)) / (N1*N2))
    lower1 = AUC1 - 1.96*SE_AUC1
    upper1 = AUC1 + 1.96*SE_AUC1
    if lower1 < 0:
        lower1 = 0
    if upper1 > 1:
        upper1 = 1
    auc1=roc_auc_score(true_y1, y_prob1)
    fpr1, tpr1, thresholds1 = roc_curve(true_y1, y_prob1)



    AUC2 = roc_auc_score(true_y2, y_prob2)
    N1 = sum(true_y2 == positive)
    N2 = sum(true_y2 != positive)
    Q1 = AUC2 / (2 - AUC2)
    Q2 = 2*AUC2**2 / (1 + AUC2)
    SE_AUC2 = sqrt((AUC2*(1 - AUC2) + (N1 - 1)*(Q1 - AUC2**2) + (N2 - 1)*(Q2 - AUC2**2)) / (N1*N2))
    lower2 = AUC2 - 1.96*SE_AUC2
    upper2 = AUC2 + 1.96*SE_AUC2
    if lower2 < 0:
        lower2 = 0
    if upper2 > 1:
        upper2 = 1
    auc2=roc_auc_score(true_y2, y_prob2)
    fpr2, tpr2, thresholds2 = roc_curve(true_y2, y_prob2)

    AUC3 = roc_auc_score(true_y3, y_prob3)
    N1 = sum(true_y3 == positive)
    N2 = sum(true_y3 != positive)
    Q1 = AUC3 / (2 - AUC3)
    Q2 = 2*AUC3**2 / (1 + AUC3)
    SE_AUC3 = sqrt((AUC3*(1 - AUC3) + (N1 - 1)*(Q1 - AUC3**2) + (N2 - 1)*(Q2 - AUC3**2)) / (N1*N2))
    lower3 = AUC3 - 1.96*SE_AUC3
    upper3 = AUC3 + 1.96*SE_AUC3
    if lower3 < 0:
        lower3 = 0
    if upper3 > 1:
        upper3 = 1
    auc3=roc_auc_score(true_y3, y_prob3)
    fpr3, tpr3, thresholds3 = roc_curve(true_y3, y_prob3)


    AUC4 = roc_auc_score(true_y4, y_prob4)
    N1 = sum(true_y4 == positive)
    N2 = sum(true_y4 != positive)
    Q1 = AUC4 / (2 - AUC4)
    Q2 = 2*AUC4**2 / (1 + AUC4)
    SE_AUC4 = sqrt((AUC4*(1 - AUC4) + (N1 - 1)*(Q1 - AUC4**2) + (N2 - 1)*(Q2 - AUC4**2)) / (N1*N2))
    lower4 = AUC4 - 1.96*SE_AUC4
    upper4 = AUC4 + 1.96*SE_AUC4
    if lower4 < 0:
        lower4 = 0
    if upper4 > 1:
        upper4 = 1
    auc4=roc_auc_score(true_y4, y_prob4)
    fpr4, tpr4, thresholds4 = roc_curve(true_y4, y_prob4)


    AUC5 = roc_auc_score(true_y5, y_prob5)
    N1 = sum(true_y5 == positive)
    N2 = sum(true_y5 != positive)
    Q1 = AUC5 / (2 - AUC5)
    Q2 = 2*AUC5**2 / (1 + AUC5)
    SE_AUC5 = sqrt((AUC5*(1 - AUC5) + (N1 - 1)*(Q1 - AUC5**2) + (N2 - 1)*(Q2 - AUC5**2)) / (N1*N2))
    lower5 = AUC5 - 1.96*SE_AUC5
    upper5 = AUC5 + 1.96*SE_AUC5
    if lower5 < 0:
        lower5 = 0
    if upper5 > 1:
        upper5 = 1
    auc5=roc_auc_score(true_y5, y_prob5)
    fpr5, tpr5, thresholds5 = roc_curve(true_y5, y_prob5)

    fig = go.Figure([
    go.Scatter(
        x          = fpr1,
        y          = tpr1,
        line       = dict(color=c_line_main1, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = '<b>'+name1+'</b>'),
    go.Scatter(
        x          = fpr1,
        y          = tpr1,
        line       = dict(color=c_i, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'AUC: {auc1:.4f}'),
    go.Scatter(
        x          = fpr1,
        y          = tpr1,
        line       = dict(color=c_i, width=0),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'(95% CI: '+f'{lower1:.4f}-{upper1:.4f})'),
    go.Scatter(
        x          = fpr2,
        y          = tpr2,
        line       = dict(color=c_line_main2, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = '<b>'+name2+'</b>'),
    go.Scatter(
        x          = fpr2,
        y          = tpr2,
        line       = dict(color=c_i, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'AUC: {auc2:.4f}'),
    go.Scatter(
        x          = fpr2,
        y          = tpr2,
        line       = dict(color=c_i, width=0),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'(95% CI: '+f'{lower2:.4f}-{upper2:.4f})'),

    go.Scatter(
        x          = fpr3,
        y          = tpr3,
        line       = dict(color=c_line_main3, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = '<b>'+name3+'</b>'),
    go.Scatter(
        x          = fpr3,
        y          = tpr3,
        line       = dict(color=c_i, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'AUC: {auc3:.4f}'),
    go.Scatter(
        x          = fpr3,
        y          = tpr3,
        line       = dict(color=c_i, width=0),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'(95% CI: '+f'{lower3:.4f}-{upper3:.4f})'),

    go.Scatter(
        x          = fpr4,
        y          = tpr4,
        line       = dict(color=c_line_main4, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = '<b>'+name4+'</b>'),
    go.Scatter(
        x          = fpr4,
        y          = tpr4,
        line       = dict(color=c_i, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'AUC: {auc4:.4f}'),
    go.Scatter(
        x          = fpr4,
        y          = tpr4,
        line       = dict(color=c_i, width=0),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'(95% CI: '+f'{lower4:.4f}-{upper4:.4f})'),

    go.Scatter(
        x          = fpr5,
        y          = tpr5,
        line       = dict(color=c_line_main5, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = '<b>'+name5+'</b>'),
    go.Scatter(
        x          = fpr5,
        y          = tpr5,
        line       = dict(color=c_i, width=3),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'AUC: {auc5:.4f}'),
    go.Scatter(
        x          = fpr5,
        y          = tpr5,
        line       = dict(color=c_i, width=0),
        hoverinfo  = "skip",
        showlegend = True,
        name       = f'(95% CI: '+f'{lower5:.4f}-{upper5:.4f})')
    ])
    fig.add_shape(
        type ='line',
        line =dict(dash='dash'),
        x0=0, x1=1, y0=0, y1=1
    )
    fig.update_layout(
        template    = 'plotly_white',
        title_x     = 1,
        xaxis_title = '<b>1-Specificity</b>',
        yaxis_title = "<b>Recall</b>",
        width       = 600,
        height      = 600,
        legend      = dict(
            yanchor="bottom",
            xanchor="right",
            x=0.95,
            y=0.01,
        )
    )
    fig.update_layout(
        font=dict(
            family="Times New Roman",
            size=14,  # Set the font size here
            color="Black"
        )
    )
    fig.update_yaxes(
        range       = [0, 1],
        gridcolor   = c_grid,
        scaleanchor = "x",
        scaleratio  = 1,
        linecolor   = 'black')
    fig.update_xaxes(
        range       = [0, 1],
        gridcolor   = c_grid,
        constrain   = 'domain',
        linecolor   = 'black')
    return fig

In [ ]:
from sklearn.metrics import precision_recall_curve, auc
from scipy.stats import norm
import plotly.graph_objects as go
import numpy as np

def ci(tp, n, alpha=0.05):
    """Estimates confidence interval for Bernoulli p"""
    p_hat = float(tp) / n
    z_score = norm.isf(alpha * 0.5)  # two sides, so alpha/2 on each side
    variance_of_sum = p_hat * (1 - p_hat) / n
    std = variance_of_sum ** 0.5
    return max(p_hat - z_score * std, 0), min(p_hat + z_score * std, 1)

def plot_pr_curve(true_y1, y_prob1, true_y2, y_prob2, true_y3, y_prob3, true_y4, y_prob4, true_y5, y_prob5, name1, name2, name3, name4, name5, positive=1):
    c_fill      = 'rgba(52, 152, 219, 0.2)'
    c_line      = 'rgba(52, 152, 219, 0.5)'
    c_line_main1 = 'rgba(250, 50, 50, 1.0)'
    c_line_main2 = 'rgba(50, 50, 250, 1.0)'
    c_line_main3 = 'rgba(20, 250, 50, 1.0)'
    c_line_main4 = 'rgba(255, 165, 0, 1.0)'
    c_line_main5 = 'rgba(0, 0, 0, 1.0)'
    c_grid      = 'rgba(5, 5, 5, 0.5)'
    c_annot     = 'rgba(149, 165, 166, 0.5)'
    c_i = 'rgba(255, 255, 255, 0)'
    c_highlight = 'rgba(192, 57, 43, 1.0)'

    def compute_pr_auc_ci(y_true, y_prob, pos_label, alpha=0.05):
        precision, recall, _ = precision_recall_curve(y_true, y_prob, pos_label=pos_label)
        pr_auc = auc(recall, precision)
        n = len(y_true)
        se_auc = np.sqrt(pr_auc * (1 - pr_auc) / n)
        z = norm.isf(alpha / 2)
        lower = pr_auc - z * se_auc
        upper = pr_auc + z * se_auc
        if lower < 0: lower = 0
        if upper > 1: upper = 1
        return precision, recall, pr_auc, lower, upper

    precision1, recall1, auc1, lower1, upper1 = compute_pr_auc_ci(true_y1, y_prob1, positive)
    precision2, recall2, auc2, lower2, upper2 = compute_pr_auc_ci(true_y2, y_prob2, positive)
    precision3, recall3, auc3, lower3, upper3 = compute_pr_auc_ci(true_y3, y_prob3, positive)
    precision4, recall4, auc4, lower4, upper4 = compute_pr_auc_ci(true_y4, y_prob4, positive)
    precision5, recall5, auc5, lower5, upper5 = compute_pr_auc_ci(true_y5, y_prob5, positive)

    fig = go.Figure([
        go.Scatter(
            x=recall1,
            y=precision1,
            line=dict(color=c_line_main1, width=3),
            hoverinfo="skip",
            showlegend=True,
            name='<b>' + name1 + '</b>'),
        go.Scatter(
            x=recall1,
            y=precision1,
            line=dict(color=c_i, width=3),
            hoverinfo="skip",
            showlegend=True,
            name=f'AUC: {auc1:.4f}'),
        go.Scatter(
            x=recall1,
            y=precision1,
            line=dict(color=c_i, width=0),
            hoverinfo="skip",
            showlegend=True,
            name=f'(95% CI: {lower1:.4f}-{upper1:.4f})'),

        go.Scatter(
            x=recall2,
            y=precision2,
            line=dict(color=c_line_main2, width=3),
            hoverinfo="skip",
            showlegend=True,
            name='<b>' + name2 + '</b>'),
        go.Scatter(
            x=recall2,
            y=precision2,
            line=dict(color=c_i, width=3),
            hoverinfo="skip",
            showlegend=True,
            name=f'AUC: {auc2:.4f}'),
        go.Scatter(
            x=recall2,
            y=precision2,
            line=dict(color=c_i, width=0),
            hoverinfo="skip",
            showlegend=True,
            name=f'(95% CI: {lower2:.4f}-{upper2:.4f})'),

        go.Scatter(
            x=recall3,
            y=precision3,
            line=dict(color=c_line_main3, width=3),
            hoverinfo="skip",
            showlegend=True,
            name='<b>' + name3 + '</b>'),
        go.Scatter(
            x=recall3,
            y=precision3,
            line=dict(color=c_i, width=3),
            hoverinfo="skip",
            showlegend=True,
            name=f'AUC: {auc3:.4f}'),
        go.Scatter(
            x=recall3,
            y=precision3,
            line=dict(color=c_i, width=0),
            hoverinfo="skip",
            showlegend=True,
            name=f'(95% CI: {lower3:.4f}-{upper3:.4f})'),

        go.Scatter(
            x=recall4,
            y=precision4,
            line=dict(color=c_line_main4, width=3),
            hoverinfo="skip",
            showlegend=True,
            name='<b>' + name4 + '</b>'),
        go.Scatter(
            x=recall4,
            y=precision4,
            line=dict(color=c_i, width=3),
            hoverinfo="skip",
            showlegend=True,
            name=f'AUC: {auc4:.4f}'),
        go.Scatter(
            x=recall4,
            y=precision4,
            line=dict(color=c_i, width=0),
            hoverinfo="skip",
            showlegend=True,
            name=f'(95% CI: {lower4:.4f}-{upper4:.4f})'),

        go.Scatter(
            x=recall5,
            y=precision5,
            line=dict(color=c_line_main5, width=3),
            hoverinfo="skip",
            showlegend=True,
            name='<b>' + name5 + '</b>'),
        go.Scatter(
            x=recall5,
            y=precision5,
            line=dict(color=c_i, width=3),
            hoverinfo="skip",
            showlegend=True,
            name=f'AUC: {auc5:.4f}'),
        go.Scatter(
            x=recall5,
            y=precision5,
            line=dict(color=c_i, width=0),
            hoverinfo="skip",
            showlegend=True,
            name=f'(95% CI: {lower5:.4f}-{upper5:.4f})')
    ])

    fig.update_layout(
        template='plotly_white',
        title_x=0.5,
        xaxis_title='<b>Recall</b>',
        yaxis_title="<b>Precision</b>",
        width=600,
        height=600,
        legend=dict(
            yanchor="top",
            xanchor="right",
            x=0.95,
            y=0.99,
        )
    )
    fig.update_layout(
        font=dict(
            family="Times New Roman",
            size=14,
            color="Black"
        )
    )
    fig.update_yaxes(
        range=[0, 1],
        gridcolor=c_grid,
        scaleanchor="x",
        scaleratio=1,
        linecolor='black'
    )
    fig.update_xaxes(
        range=[0, 1],
        gridcolor=c_grid,
        constrain='domain',
        linecolor='black'
    )
    return fig




In [ ]:
plot_roc_curve(y_test, preds_sgd, y_test, preds_adam, y_test, [item[1] for item in preds_lr], y_test, [item[1] for item in preds_svc_linear], y_test, [item[1] for item in preds_svc_rbf], 'NN-SGD', 'NN-Adam', 'LR', 'Linear SVM', 'SVM-RBF')

In [ ]:
plot_pr_curve(y_test, preds_sgd, y_test, preds_adam, y_test, [item[1] for item in preds_lr], y_test, [item[1] for item in preds_svc_linear], y_test, [item[1] for item in preds_svc_rbf], 'NN-SGD', 'NN-Adam', 'LR', 'Linear SVM', 'SVM-RBF')

In [102]:
df=pd.read_stata('NSDUH_2020.dta')
df['BMI2']=pd.to_numeric(df['BMI2'], errors='coerce')

df['NEWRACE2'] = df['NEWRACE2'].replace('1 - NonHisp White','White')
df['NEWRACE2'] = df['NEWRACE2'].replace('2 - NonHisp Black/Afr Am','Black')
df['NEWRACE2'] = df['NEWRACE2'].replace('3 - NonHisp Native Am/AK Native','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('4 - NonHisp Native HI/Other Pac Isl','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('5 - NonHisp Asian','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('6 - NonHisp more than one race','Others')
df['NEWRACE2'] = df['NEWRACE2'].replace('7 - Hispanic','Others')

data=df[['NEWRACE2', 'INCOME' ,'ADDPREV','OXCOPDAPYU', 'OXYMPDAPYU', 'HYDCPDAPYU', 'HYDMPDAPYU', 'FENTPDAPYU',
         'MORPPDAPYU', 'CODEPDAPYU', 'MTDNPDAPYU', 'TRAMPDAPYU', 'BUPRPDAPYU',
         'HEREVER','TXEVRRCVD','DIABETEVR', 'COPDEVER', 'CIRROSEVR', 'HEPBCEVER',
         'KIDNYDSEV', 'ASTHMAEVR', 'HIVAIDSEV', 'CANCEREVR','IRSEX', 'IRMARIT', 'WRK35WKUS', 'UDPYOPI']]

data=pd.get_dummies(data)

data=data.drop(['INCOME_2 - $20,000 - $49,999', 'INCOME_3 - $50,000 - $74,999',  'INCOME_4 - $75,000 or More', 'ADDPREV_85 - BAD DATA Logically assigned', 'ADDPREV_94 - DON T KNOW', 'ADDPREV_97 - REFUSED', 'ADDPREV_98 - BLANK',
                'ADDPREV_99 - LEGITIMATE SKIP', 'IRSEX_2 - Female',
                'OXCOPDAPYU_0 - No/Unknown', 'OXYMPDAPYU_0 - No/Unknown', 'HYDCPDAPYU_0 - No/Unknown', 'HYDMPDAPYU_0 - No/Unknown',
               'FENTPDAPYU_0 - No/Unknown', 'MORPPDAPYU_0 - No/Unknown', 'CODEPDAPYU_0 - No/Unknown', 'MTDNPDAPYU_0 - No/Unknown',
               'TRAMPDAPYU_0 - No/Unknown', 'BUPRPDAPYU_0 - No/Unknown', 'HEREVER_94 - DON T KNOW',
'HEREVER_97 - REFUSED', 'TXEVRRCVD_85 - BAD DATA Logically assigned',
'TXEVRRCVD_91 - NEVER USED ALCOHOL OR DRUGS','TXEVRRCVD_94 - DON T KNOW','TXEVRRCVD_97 - REFUSED','TXEVRRCVD_98 - BLANK',
                'DIABETEVR_85 - BAD DATA Logically assigned'
,'DIABETEVR_94 - DON T KNOW','DIABETEVR_97 - REFUSED','DIABETEVR_98 - BLANK','DIABETEVR_99 - LEGITIMATE SKIP',
                'COPDEVER_85 - BAD DATA Logically assigned','COPDEVER_94 - DON T KNOW','COPDEVER_97 - REFUSED'
,'COPDEVER_98 - BLANK','COPDEVER_99 - LEGITIMATE SKIP', 'CIRROSEVR_85 - BAD DATA Logically assigned'
,'CIRROSEVR_94 - DON T KNOW','CIRROSEVR_97 - REFUSED','CIRROSEVR_98 - BLANK','CIRROSEVR_99 - LEGITIMATE SKIP',
                'HEPBCEVER_85 - BAD DATA Logically assigned','HEPBCEVER_94 - DON T KNOW','HEPBCEVER_97 - REFUSED'
,'HEPBCEVER_98 - BLANK','HEPBCEVER_99 - LEGITIMATE SKIP'
,'KIDNYDSEV_85 - BAD DATA Logically assigned','KIDNYDSEV_94 - DON T KNOW','KIDNYDSEV_97 - REFUSED','KIDNYDSEV_98 - BLANK'
,'KIDNYDSEV_99 - LEGITIMATE SKIP','ASTHMAEVR_85 - BAD DATA Logically assigned','ASTHMAEVR_94 - DON T KNOW','ASTHMAEVR_97 - REFUSED',
'ASTHMAEVR_98 - BLANK','ASTHMAEVR_99 - LEGITIMATE SKIP', 'HIVAIDSEV_85 - BAD DATA Logically assigned'
,'HIVAIDSEV_94 - DON T KNOW','HIVAIDSEV_97 - REFUSED','HIVAIDSEV_98 - BLANK','HIVAIDSEV_99 - LEGITIMATE SKIP',
              'CANCEREVR_85 - BAD DATA Logically assigned','CANCEREVR_94 - DON T KNOW','CANCEREVR_97 - REFUSED'
,'CANCEREVR_98 - BLANK','CANCEREVR_99 - LEGITIMATE SKIP'
,'WRK35WKUS_85 - BAD DATA Logically assigned','WRK35WKUS_94 - DON T KNOW','WRK35WKUS_97 - REFUSED','WRK35WKUS_98 - BLANK'
,'WRK35WKUS_99 - LEGITIMATE SKIP', 'UDPYOPI_0 - No', 'IRMARIT_99 - LEGITIMATE SKIP Respondent is <= 14 years old'
               ], axis=1)

data

NEWRACE2_White  NEWRACE2_Black  NEWRACE2_Others  \
0                True           False            False   
1                True           False            False   
2               False           False             True   
3                True           False            False   
4                True           False            False   
...               ...             ...              ...   
32888            True           False            False   
32889            True           False            False   
32890           False           False             True   
32891            True           False            False   
32892            True           False            False   

       INCOME_1 - Less than $20,000  ADDPREV_1 - Yes  ADDPREV_2 - No  \
0                             False            False            True   
1                             False            False            True   
2                             False             True           False   
3                             False            False            True   
4                             False            False           False   
...                             ...              ...             ...   
32888                         False             True           False   
32889                         False             True           False   
32890                         False            False           False   
32891                         False             True           False   
32892                         False             True           False   

       OXCOPDAPYU_1 - Yes  OXYMPDAPYU_1 - Yes  HYDCPDAPYU_1 - Yes  \
0                   False               False               False   
1                   False               False                True   
2                   False               False                True   
3                   False               False               False   
4                   False               False               False   
...                   ...                 ...                 ...   
32888               False               False               False   
32889               False               False               False   
32890               False               False               False   
32891               False               False               False   
32892               False               False                True   

       HYDMPDAPYU_1 - Yes  ...  CANCEREVR_1 - Yes  CANCEREVR_2 - No  \
0                   False  ...              False              True   
1                   False  ...              False             False   
2                   False  ...              False             False   
3                   False  ...              False              True   
4                   False  ...              False              True   
...                   ...  ...                ...               ...   
32888               False  ...              False              True   
32889               False  ...              False              True   
32890               False  ...              False             False   
32891               False  ...              False             False   
32892               False  ...              False              True   

       IRSEX_1 - Male  IRMARIT_1 - Married  IRMARIT_2 - Widowed  \
0                True                False                False   
1                True                False                False   
2               False                False                False   
3                True                 True                False   
4                True                False                False   
...               ...                  ...                  ...   
32888            True                False                False   
32889            True                 True                False   
32890           False                False                False   
32891           False                False                False   
32892           False     

In [103]:
d_pos=data[data['UDPYOPI_1 - Yes'].isin([1])]
d_neg=data[data['UDPYOPI_1 - Yes'].isin([0])]
data=pd.concat([d_pos, d_neg])
data.to_csv('Dataset2.csv')
data.replace({True: 1, False: 0}, inplace=True)

X=data.drop(['UDPYOPI_1 - Yes'], axis=1)
y=data['UDPYOPI_1 - Yes']

df1=df[['BMI2']]

X=pd.concat([X, df1], axis=1)

X=X.fillna(0)

X

NEWRACE2_White  NEWRACE2_Black  NEWRACE2_Others  \
193                 1               0                0   
258                 1               0                0   
430                 0               0                1   
776                 1               0                0   
887                 1               0                0   
...               ...             ...              ...   
32888               1               0                0   
32889               1               0                0   
32890               0               0                1   
32891               1               0                0   
32892               1               0                0   

       INCOME_1 - Less than $20,000  ADDPREV_1 - Yes  ADDPREV_2 - No  \
193                               0                0               0   
258                               0                1               0   
430                               0                0               0   
776                               0                1               0   
887                               0                1               0   
...                             ...              ...             ...   
32888                             0                1               0   
32889                             0                1               0   
32890                             0                0               0   
32891                             0                1               0   
32892                             0                1               0   

       OXCOPDAPYU_1 - Yes  OXYMPDAPYU_1 - Yes  HYDCPDAPYU_1 - Yes  \
193                     1                   0                   1   
258                     1                   0                   1   
430                     1                   0                   1   
776                     0                   0                   0   
887                     0                   0                   0   
...                   ...                 ...                 ...   
32888                   0                   0                   0   
32889                   0                   0                   0   
32890                   0                   0                   0   
32891                   0                   0                   0   
32892                   0                   0                   1   

       HYDMPDAPYU_1 - Yes  ...  CANCEREVR_1 - Yes  CANCEREVR_2 - No  \
193                     0  ...                  0                 0   
258                     0  ...                  0                 1   
430                     0  ...                  0                 0   
776                     0  ...                  0                 1   
887                     0  ...                  0                 0   
...                   ...  ...                ...               ...   
32888                   0  ...                  0                 1   
32889                   0  ...                  0                 1   
32890                   0  ...                  0                 0   
32891                   0  ...                  0                 0   
32892                   0  ...                  0                 1   

       IRSEX_1 - Male  IRMARIT_1 - Married  IRMARIT_2 - Widowed  \
193                 0                    0                    0   
258                 1                    1                    0   
430                 1                    0                    0   
776                 0                    0                    0   
887                 1                    0                    0   
...               ...                  ...                  ...   
32888               1                    0                    0   
32889               1                    1                    0   
32890               0                    0                    0   
32891               0                    0                    0   
32892               0     

In [104]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=43, stratify=y) # Use stratify to have the same proportion of each class

class_weights = compute_class_weight(
                                        class_weight = "balanced",
                                        classes = np.unique(y_train),
                                        y = y_train
                                    )
sklearn_weights = dict(enumerate(class_weights))
sklearn_weights

{0: 0.5031742389475294, 1: 79.25903614457832}

In [105]:
network_sgd = load_model('best_model_sgd.h5')
network_adam = load_model('best_model_adam.h5')

In [107]:
from sklearn.linear_model import LogisticRegression
logit = LogisticRegression(max_iter=1000000, class_weight=sklearn_weights)
logit_model=logit.fit(X_train, y_train)

In [108]:
import pickle
filename = 'LR_Regular.sav'

with open(filename, 'wb') as file:
    pickle.dump(logit_model, file)

In [109]:
from sklearn.svm import LinearSVC
svc_linear=LinearSVC(C=1, class_weight=sklearn_weights, dual=False, max_iter=1000000)
svc_linear=svc_linear.fit(X_train, y_train)

In [110]:
filename = 'SVC_Linear_Regular.sav'

with open(filename, 'wb') as file:
    pickle.dump(svc_linear, file)

In [111]:
from sklearnex import patch_sklearn
patch_sklearn()

Intel(R) Extension for Scikit-learn* enabled (https://github.com/intel/scikit-learn-intelex)


In [112]:
from sklearn.svm import SVC
svc_rbf = SVC(C=1, kernel='rbf', class_weight=sklearn_weights, probability=True, max_iter=1000000)
svc_rbf = svc_rbf.fit(X_train, y_train)

In [113]:
filename = 'SVC_RBF_Regular.sav'

with open(filename, 'wb') as file:
    pickle.dump(svc_rbf, file)

In [114]:
preds_sgd=network_sgd.predict(X_test)
preds_adam=network_adam.predict(X_test)
preds_lr=logit_model.predict_proba(X_test)
preds_svc_linear=svc_linear._predict_proba_lr(X_test)
preds_svc_rbf=svc_rbf.predict_proba(X_test)

206/206 [==============================] - 1s 4ms/step


In [115]:
plot_roc_curve(y_test, preds_sgd, y_test, preds_adam, y_test, [item[1] for item in preds_lr], y_test, [item[1] for item in preds_svc_linear], y_test, [item[1] for item in preds_svc_rbf], 'NN-SGD', 'NN-Adam', 'LR', 'Linear SVM', 'SVM-RBF')

In [116]:
plot_pr_curve(y_test, preds_sgd, y_test, preds_adam, y_test, [item[1] for item in preds_lr], y_test, [item[1] for item in preds_svc_linear], y_test, [item[1] for item in preds_svc_rbf], 'NN-SGD', 'NN-Adam', 'LR', 'Linear SVM', 'SVM-RBF')